# **Viet Fact Check Base Line Model**

## **Prepare enviroment**

In [1]:
!rm -r sample_data

rm: cannot remove 'sample_data': No such file or directory


In [2]:
# Dùng để tải file env. và file requirements. txt chạy trên colab
# !pip freeze > requirements.txt # sinh file requirements.txt
from google.colab import files
from dotenv import load_dotenv

print("Chọn file .env để upload")
uploaded = files.upload()  # chọn file .env từ máy
load_dotenv(".env") # load biến môi trường từ file .env

Chọn file .env để upload


Saving .env to .env (1)


True

In [3]:
print("Choose file requirements.txt to upload")
uploaded = files.upload()  # chọn file requirements.txt từ máy
load_dotenv("requirements.txt") # load danh sách thư viện từ file requirements.txt

Choose file requirements.txt to upload


Saving requirements.txt to requirements (1).txt


True

In [4]:
!pip install -r requirements.txt --upgrade

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 23.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 22.9 MB/s eta 0:00:00
  Cloning https://github.com/googlecolab/kernel_gateway (to revision b134e9945df25c2dcb98ade9129399be10788671) to /tmp/pip-install-eztzkrrv/jupyter-kernel-gateway_8522d90d33c644a4819c52340dbf891f
  Running command git clone --filter=blob:none --quiet https://github.com/googlecolab/kernel_gateway /tmp/pip-install-eztzkrrv/jupyter-kernel-gateway_8522d90d33c644a4819c52340dbf891f
  Running command git rev-parse -q --verify 'sha^b134e9945df25c2dcb98ade9129399be10788671'
  Running command git fetch -q https://github.com/googlecolab/kernel_gateway b134e9945df25c2dcb98ade9129399be10788671
  Running command git checkout -q b134e9945df25c2dcb98ade9129399be10788671
  Resolved https://github.com/googlecolab/kernel_gateway to commit b134e9945df25c2dcb98ade9129399be10788671
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━

In [5]:
import os
from dotenv import load_dotenv
from azure.ai.inference import ChatCompletionsClient
from azure.core.credentials import AzureKeyCredential
from azure.ai.inference.models import SystemMessage, UserMessage

In [6]:
load_dotenv(".env") # load biến môi trường từ file .env
endpoint = "https://models.github.ai/inference"
model = "openai/gpt-4o-mini"
token = os.environ["GITHUB_TOKEN"]

client = ChatCompletionsClient(
    endpoint=endpoint,
    credential=AzureKeyCredential(token),
)

## **I. Input & Preprocessing**

- Input: Một đoạn văn bản ngắn tiếng Việt.
- Output: Đoạn văn bản tiếng Việt đã được tiền xử lý đưa về tiếng Việt chuẩn phổ thông.

In [ ]:
import os
from azure.ai.inference import ChatCompletionsClient
from azure.ai.inference.models import SystemMessage, UserMessage
from azure.core.credentials import AzureKeyCredential
from dotenv import load_dotenv

load_dotenv(".env") # load biến môi trường từ file .env

SYSTEM_PROMPT = "Ghi lại những gì người dùng nhập vào nhưng đúng chính tả và ngữ pháp. Đối với các từ viết tắt hãy ghi ra đầy đủ. Những từ lóng, teencode, từ tiếng Việt nhưng viết không dấu, ... hãy chuyển về ngôn ngữ phổ thông."

INPUT_TEXT = """Troi oi, hom nay nong qua di
Tôi tin rằng biến đổi khí hậu đang làm thời tiết cực đoan hơn.
Bn khỏe hông
Nhiệt độ toàn cầu đã tăng 1.1°C trong 100 năm qua"""

PROCESSED_TEXT = ""

endpoint = "https://models.github.ai/inference"
model = "openai/gpt-4o-mini"
token = os.environ["GITHUB_TOKEN"]

client = ChatCompletionsClient(
    endpoint=endpoint,
    credential=AzureKeyCredential(token),
)

response = client.complete(
    messages=[
        SystemMessage(SYSTEM_PROMPT),
        UserMessage(INPUT_TEXT),
    ],
    model=model
)

PROCESSED_TEXT=response.choices[0].message.content

print(PROCESSED_TEXT)

Trời ơi, hôm nay nóng quá đi.  
Tôi tin rằng biến đổi khí hậu đang làm thời tiết cực đoan hơn.  
Bạn khỏe không?  
Nhiệt độ toàn cầu đã tăng 1.1°C trong 100 năm qua.


- [Hướng dẫn sử dụng API của Github hỗ trợ](https://www.youtube.com/watch?v=YP8mV_2RDLc)
- [Github Models Usage Guide](https://docs.github.com/en/github-models/use-github-models/prototyping-with-ai-models#rate-limits)

## **II. Claim Detection**

- Input: Đoạn văn bản tiếng Việt đã được tiền xử lý đưa về tiếng Việt chuẩn phổ thông.
- Output: Đoạn văn bản chứa các claim (khẳng định, luận điểm, sự thật có thể kiểm chứng) đã lược bỏ phần dư thừa và không cần thiết.

In [8]:
import os
from azure.ai.inference import ChatCompletionsClient
from azure.ai.inference.models import SystemMessage, UserMessage
from azure.core.credentials import AzureKeyCredential

SYSTEM_PROMPT = """
Bạn là mô-đun Claim Detection.

Nhiệm vụ:
- Giữ lại và trả về những câu có chứa claim: phát biểu khẳng định, luận điểm hoặc sự thật có thể kiểm chứng đúng/sai.
- Bỏ đi các câu cảm thán, chào hỏi, xã giao hoặc câu không chứa claim.

Yêu cầu chi tiết:
- Một claim phải là một mệnh đề có thông tin khách quan, có thể kiểm chứng được (fact hoặc assertion).
- Nếu câu có chứa từ ngữ như "tôi tin rằng", "theo tôi nghĩ", "có lẽ", hãy bỏ phần mở đầu đó và chỉ giữ lại nội dung khẳng định chính.
- Kết quả cần giữ nguyên ngữ pháp, chính tả, tiếng Việt chuẩn."""

CLAIM_TEXT = ""

endpoint = "https://models.github.ai/inference"
model = "openai/gpt-4o-mini"
token = os.environ["GITHUB_TOKEN"]

client = ChatCompletionsClient(
    endpoint=endpoint,
    credential=AzureKeyCredential(token),
)

response = client.complete(
    messages=[
        SystemMessage(SYSTEM_PROMPT),
        UserMessage(PROCESSED_TEXT),
    ],
    model=model
)

CLAIM_TEXT = response.choices[0].message.content

print(CLAIM_TEXT)

Biến đổi khí hậu đang làm thời tiết cực đoan hơn.  
Nhiệt độ toàn cầu đã tăng 1.1°C trong 100 năm qua.


## **III. Document Retrieval**

- Input: Danh sách các claim (chuỗi văn bản tiếng Việt ngắn) được tạo ra từ Module 2 (sau khi đã tiền xử lý và tách các khẳng định có thể kiểm chứng).
- Output: Tập hợp kết quả truy xuất tài liệu cho từng claim bao gồm tiêu đề, đường dẫn, và đoạn mô tả ngắn (snippet) của các bài viết từ Google Search.

In [11]:
!pip install tldextract
!pip install ddgs

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 107.4/107.4 kB 3.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 41.6/41.6 kB 1.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.3/5.3 MB 39.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 74.1 MB/s eta 0:00:00
  Attempting uninstall: lxml
    Found existing installation: lxml 5.4.0
    Uninstalling lxml-5.4.0:
      Successfully uninstalled lxml-5.4.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
htmldate 1.9.3 requires lxml<6,>=5.3.0; platform_system != "Darwin" or python_version > "3.8", but you have lxml 6.0.2 which is incompatible.


In [12]:
import os
import json
import re
import time
from dotenv import load_dotenv
from tqdm import tqdm
from concurrent.futures import ThreadPoolExecutor, as_completed
import tldextract
from sentence_transformers import SentenceTransformer, util
from ddgs import DDGS

from azure.ai.inference import ChatCompletionsClient
from azure.ai.inference.models import SystemMessage, UserMessage
from azure.core.credentials import AzureKeyCredential

load_dotenv()
embedder = SentenceTransformer("keepitreal/vietnamese-sbert")
GITHUB_TOKEN = os.getenv("GITHUB_TOKEN")

MODEL = "openai/gpt-4o-mini"
client = ChatCompletionsClient(
    endpoint="https://models.github.ai/inference",
    credential=AzureKeyCredential(GITHUB_TOKEN),
)

TRUSTED_DOMAINS = [
    # Việt Nam
    "vnexpress.net", "tuoitre.vn", "thanhnien.vn", "nhandan.vn",
    "moh.gov.vn", "suckhoedoisong.vn", "zingnews.vn",
    "vietnamnet.vn", "baochinhphu.vn", "cafef.vn", "monre.gov.vn",

    # Quốc tế
    "bbc.com", "reuters.com", "apnews.com", "theguardian.com",
    "cnn.com", "nytimes.com", "who.int", "un.org",
    "worldbank.org", "nature.com", "sciencedirect.com"
]

BAD_DOMAINS = [
    # Blog cá nhân & nền tảng tạo blog miễn phí
    "blogspot", "wordpress", "weebly", "wixsite", "jimdo", "tumblr",

    # Mạng xã hội & chia sẻ video
    "facebook", "twitter", "tiktok", "instagram", "youtube", "reddit", "pinterest",

    # Diễn đàn, hỏi đáp, chia sẻ linh tinh
    "voz.vn", "quora", "reddit", "kenh14", "webtretho", "otofun", "tinhte.vn",

    # Trang từ điển / wiki không chính thống
    "tudientiengviet", "wiktionary", "vi.wiktionary", "tratu.soha.vn", "vdict",

    # Trang học sinh – chia sẻ bài làm / học liệu chưa kiểm chứng
    "hocmai", "loigiaihay", "olm.vn", "giaibaitap", "baitap123", "hoc24",

    # Nguồn tin rác / spam nội dung tổng hợp
    "eva.vn", "2sao.vn", "afamily.vn", "tiin.vn", "yeah1", "bestie.vn", "blogtamsu",
]

# 1. Sinh truy vấn mở rộng (tự động hoặc thủ công)
def expand_query(claim: str) -> list[str]:
    """Sinh các biến thể tìm kiếm từ claim."""
    prompt = f"""
    Sinh ra 3-5 phiên bản khác nhau của câu truy vấn sau để tìm kiếm web.
    - Viết lại tự nhiên, cùng nghĩa.
    - Không thêm ý mới.
    - Giữ ngắn gọn, phù hợp tìm kiếm.

    Truy vấn gốc: "{claim}"

    Trả về JSON array duy nhất như:
    ["biến thể 1", "biến thể 2", "biến thể 3", ...]
    """

    response = client.complete(
        messages=[
            SystemMessage("Bạn chỉ trả về JSON array, KHÔNG có giải thích."),
            UserMessage(prompt)
        ],
        model=MODEL,
        temperature=0.7
    )

    content = response.choices[0].message.content.strip()

    try:
        expanded = json.loads(content)
        if not isinstance(expanded, list):
            raise ValueError
    except Exception:
        m = re.search(r'\[.*\]', content, re.S)
        expanded = json.loads(m.group(0)) if m else [claim]

    expanded += [
        claim,
        f"{claim} site:vnexpress.net OR site:tuoitre.vn OR site:thanhnien.vn "
        f"OR site:nhandan.vn OR site:moh.gov.vn OR site:suckhoedoisong.vn"
    ]
    return list(dict.fromkeys(expanded))

# 2. DuckDuckGo Search
def duckduckgo_search(query: str, num_results: int = 5) -> list[dict]:
    results = []
    try:
        with DDGS() as ddgs:
            for r in ddgs.text(query, max_results=num_results):
                results.append({
                    "title": r.get("title", ""),
                    "link": r.get("href", ""),
                    "snippet": r.get("body", "")
                })
    except Exception as e:
        print(f"[DuckDuckGo error] {query[:40]}...: {e}")
    return results[:num_results]

# 3. Tính độ tin cậy (Trust Score)
def compute_trust_score(claim: str, source: dict) -> float:
    """Tính điểm tin cậy (trust_score) cho nguồn tin dựa trên:
    - sim: độ tương đồng ngữ nghĩa giữa claim và snippet (0–1)
    - overlap: tỉ lệ trùng lặp từ khóa giữa claim và snippet
    - domain_bonus: cộng điểm nếu domain uy tín (+0.25)
    - penalty: trừ điểm nếu domain kém tin cậy (-0.3)
    - lang_bonus: cộng nếu snippet là tiếng Việt (+0.1), trừ nếu không (-0.1)
    => trust_score = 0.5*sim + 0.2*overlap + domain_bonus + lang_bonus - penalty
    (giới hạn trong [0,1])
    """
    link = source.get("link", "")
    snippet = source.get("snippet", "")
    domain = tldextract.extract(link).top_domain_under_public_suffix

    # Semantic similarity
    try:
        emb_claim = embedder.encode(claim, convert_to_tensor=True)
        emb_snip = embedder.encode(snippet, convert_to_tensor=True)
        sim = util.cos_sim(emb_claim, emb_snip).item()
    except Exception:
        sim = 0.0

    # Keyword overlap
    claim_words = set(re.findall(r'\w+', claim.lower()))
    snip_words = set(re.findall(r'\w+', snippet.lower()))
    overlap = len(claim_words & snip_words) / len(claim_words) if claim_words else 0

    # Domain-based reward / penalty
    domain_bonus = 0
    penalty = 0

    if any(d in domain for d in TRUSTED_DOMAINS):
        domain_bonus += 0.25
    elif any(d in domain for d in BAD_DOMAINS):
        penalty += 0.3

    # Language bonus (phát hiện tiếng Việt)
    vietnamese_chars = re.findall(r'[àáạảãâầấậẩẫăằắặẳẵèéẹẻẽêềếệểễìíịỉĩòóọỏõôồốộổỗơờớợởỡùúụủũưừứựửữỳýỵỷỹđ]', snippet)
    lang_bonus = 0.1 if len(vietnamese_chars) > 5 else -0.1  # trừ nếu snippet không phải tiếng Việt

    # Tổng hợp (chuẩn hóa 0–1)
    trust_score = 0.5 * sim + 0.2 * overlap + domain_bonus + lang_bonus - penalty
    trust_score = max(0, min(trust_score, 1))  # giới hạn [0,1]
    return round(trust_score, 3)

# 4. Pipeline cho 1 claim
def process_claim(claim: str) -> list[dict]:
    queries = expand_query(claim)
    print(f"\n=== Claim: {claim}")
    print(f"Sinh {len(queries)} truy vấn mở rộng.\n")

    results = []
    with ThreadPoolExecutor(max_workers=4) as executor:
        futures = {executor.submit(duckduckgo_search, q): q for q in queries}
        for f in tqdm(as_completed(futures), total=len(futures), desc=f"Tìm kiếm '{claim[:40]}...'"):
            results.extend(f.result())
            time.sleep(0.1)

    # Lọc trùng link và loại bỏ link không hợp lệ
    filtered = []
    seen = set()
    for r in results:
        link = r.get("link")
        if not link or not link.startswith("http"):
            continue
        if link in seen:
            continue
        seen.add(link)

        domain = tldextract.extract(link).top_domain_under_public_suffix

        if not domain:  # bỏ link rác
            continue

        filtered.append(r)

    # Tính trust score
    for src in filtered:
        src["trust_score"] = compute_trust_score(claim, src)

    sorted_sources = sorted(filtered, key=lambda x: x["trust_score"], reverse=True)
    return sorted_sources[:5]

# 5. Chạy toàn bộ pipeline
def run_pipeline(claims: list[str]):
    all_results = []
    for claim in claims:
        claim = claim.strip()
        if not claim:
            continue
        sources = process_claim(claim)
        all_results.append({
            "claim": claim,
            "sources": sources
        })

    output_file = "document_retrieval_results_duckduckgo_v2.json"
    with open(output_file, "w", encoding="utf-8") as f:
        json.dump(all_results, f, ensure_ascii=False, indent=2)
    print(f"\nHoàn tất! Kết quả được lưu tại: {output_file}")

modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/122 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/752 [00:00<?, ?B/s]

...

bpe.codes: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/540M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/17.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/150 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [13]:
claims = [c.strip() for c in CLAIM_TEXT.split("\n") if c.strip()]
run_pipeline(claims)


=== Claim: Biến đổi khí hậu đang làm thời tiết cực đoan hơn.
Sinh 7 truy vấn mở rộng.




Tìm kiếm 'Biến đổi khí hậu đang làm thời tiết cực ...':   0%|          | 0/7 [00:00<?, ?it/s]
Tìm kiếm 'Biến đổi khí hậu đang làm thời tiết cực ...':  14%|█▍        | 1/7 [00:00<00:04,  1.22it/s]
Tìm kiếm 'Biến đổi khí hậu đang làm thời tiết cực ...':  29%|██▊       | 2/7 [00:02<00:05,  1.07s/it]
Tìm kiếm 'Biến đổi khí hậu đang làm thời tiết cực ...':  43%|████▎     | 3/7 [00:02<00:03,  1.09it/s]
Tìm kiếm 'Biến đổi khí hậu đang làm thời tiết cực ...':  57%|█████▋    | 4/7 [00:02<00:01,  1.66it/s]
Tìm kiếm 'Biến đổi khí hậu đang làm thời tiết cực ...':  71%|███████▏  | 5/7 [00:03<00:00,  2.36it/s]
Tìm kiếm 'Biến đổi khí hậu đang làm thời tiết cực ...':  86%|████████▌ | 6/7 [00:03<00:00,  1.79it/s]
Tìm kiếm 'Biến đổi khí hậu đang làm thời tiết cực ...': 100%|██████████| 7/7 [00:03<00:00,  1.77it/s]



=== Claim: Nhiệt độ toàn cầu đã tăng 1.1°C trong 100 năm qua.
Sinh 6 truy vấn mở rộng.



Tìm kiếm 'Nhiệt độ toàn cầu đã tăng 1.1°C trong 10...': 100%|██████████| 6/6 [00:02<00:00,  2.33it/s]



Hoàn tất! Kết quả được lưu tại: document_retrieval_results_duckduckgo_v2.json


## **IV. Evidence Selection**

In [14]:
!pip install playwright
!pip install playwright-stealth
!playwright install
!playwright install-deps
!pip install pdfplumber
!pip install trafilatura

173.7 MiB [] 0% 0.0s173.7 MiB [] 0% 75.8s173.7 MiB [] 0% 213.9s173.7 MiB [] 0% 154.9s173.7 MiB [] 0% 194.7s173.7 MiB [] 0% 124.6s173.7 MiB [] 0% 130.2s173.7 MiB [] 0% 98.2s173.7 MiB [] 0% 80.0s173.7 MiB [] 0% 59.7s173.7 MiB [] 0% 49.2s173.7 MiB [] 0% 37.3s173.7 MiB [] 0% 28.1s173.7 MiB [] 1% 29.4s173.7 MiB [] 1% 22.0s173.7 MiB [] 1% 17.0s173.7 MiB [] 2% 16.9s173.7 MiB [] 2% 14.1s173.7 MiB [] 3% 12.1s173.7 MiB [] 3% 12.4s173.7 MiB [] 3% 11.0s173.7 MiB [] 4% 10.0s173.7 MiB [] 4% 10.2s173.7 MiB [] 4% 9.4s173.7 MiB [] 5% 8.9s173.7 MiB [] 5% 9.0s173.7 MiB [] 6% 8.0s173.7 MiB [] 7% 7.3s173.7 MiB [] 8% 6.9s173.7 MiB [] 8% 6.8s173.7 MiB [] 9% 6.5s173.7 MiB [] 10% 6.5s173.7 MiB [] 10% 6.1s173.7 MiB [] 10% 6.2s173.7 MiB [] 11% 6.2s173.7 MiB [] 11% 6.0s173.7 MiB [] 12% 5.9s173.7 MiB [] 12% 5.7s173.7 MiB [] 13% 5.7s173.7 MiB [] 13% 5.5s173.7 MiB [] 14% 5.5s173.7 MiB [] 15% 5.3s173.7 MiB [] 16% 5.2s173.7 MiB [] 17% 5.0s173.7 MiB [] 18% 4.9s173.7 MiB [] 19% 4.7s173.7 MiB [] 20% 4.6s173.7 MiB [] 21% 

In [15]:
import requests
from pdfminer.high_level import extract_text
import asyncio
import aiohttp
import json

In [16]:
async def extract_text_from_pdf(url: str, session: aiohttp.ClientSession) -> str | None:
    """
    Tải file PDF từ URL và trích xuất văn bản nhanh bằng pdfminer.six (dùng session async)
    """
    print(f"  -> Detect PDF link. Handle by pdfminer.six: {url}")
    try:
        async with session.get(url, timeout=60) as response:
            if response.status != 200:
                print(f"❌ Failed to download PDF ({response.status})")
                return None

            data = await response.read()

        text = extract_text(io.BytesIO(data))
        print("✅ SUCCESS! Extracted text using pdfminer.six ---")
        return text.strip()

    except Exception as e:
        print(f"❌ Error when open file PDF {url}: {e}")
        return None

In [17]:
from playwright.async_api import async_playwright
from playwright_stealth import Stealth
import trafilatura

In [18]:
async def extract_text_from_web(url: str, session: aiohttp.ClientSession) -> str | None:
    """
    Thử dùng trafilatura để trích xuất nội dung trước, nếu có lỗi
    thì dùng Playwright hoặc Stealth Playwright để lấy nội dung HTML.
    """
    print(f"  -> Detect web link. Handle by Trafilatura: {url}")

    try:
        # Fetch HTML bằng session (nhanh hơn nhiều so với trafilatura.fetch_url)
        async with session.get(url, timeout=30) as resp:
            if resp.status != 200:
                raise ValueError(f"HTTP {resp.status}")
            html_content = await resp.text()

        text = trafilatura.extract(html_content)
        if text:
            print("✅ SUCCESS! Extracted text using Trafilatura ---")
            return text

        raise ValueError("Trafilatura extraction return None")

    except Exception as e:
        print(f"⚠️ Error using Trafilatura for URL {url}: {e}")
        print(f"Falling back to Playwright extraction ...")

        try:
            async with async_playwright() as p:
                browser = await p.chromium.launch(headless=True)
                page = await browser.new_page()

                await page.goto(url, timeout=15000, wait_until="domcontentloaded")
                html_content = await page.content()
                await browser.close()

                if not html_content:
                    return None

                # Nếu bị Cloudflare block, fallback stealth
                if "Cloudflare Ray ID" in html_content:
                    print("⚠️ Detected Cloudflare! Retrying with Stealth...")
                    async with Stealth().use_async(async_playwright()) as p2:
                        browser = await p2.chromium.launch(headless=True)
                        page = await browser.new_page()
                        await page.goto(url, timeout=20000)
                        html_content = await page.content()
                        await browser.close()

                main_text = trafilatura.extract(html_content, include_comments=False)
                print(f"✅ SUCCESS! Extracted text using Playwright ---")
                return main_text

        except Exception as e1:
            print(f"❌ Error using Playwright extraction for URL {url}: {e1}")
            return None

In [19]:
async def fetch_content_from_url(url: str, session: aiohttp.ClientSession) -> str | None:
    """
    Hàm điều phối: Kiểm tra loại URL và gọi hàm xử lý tương ứng.
    """
    if url.lower().endswith('.pdf'):
        return await extract_text_from_pdf(url, session)
    else:
        return await extract_text_from_web(url, session)

In [20]:
import re

def clean_text(text: str) -> str:
    """
    Hàm để làm sạch văn bản thô:
    - Loại bỏ URL và địa chỉ email.
    - Thay thế nhiều ký tự xuống dòng, tab bằng một dấu cách.
    - Xóa các dấu cách thừa.
    """
    if not text:
        return ""

    # Loại bỏ URL
    text = re.sub(r'https?://\S+|www\.\S+', '', text)

    # Loại bỏ địa chỉ email
    text = re.sub(r'\S+@\S+', '', text)

    # Thay thế các ký tự xuống dòng, tab, và các loại khoảng trắng khác bằng một dấu cách
    text = re.sub(r'[\n\r\t\xa0]+', ' ', text)

    # Thay thế nhiều dấu cách liên tiếp bằng một dấu cách duy nhất
    text = re.sub(r'\s{2,}', ' ', text)

    # Xóa dấu cách ở đầu và cuối chuỗi
    return text.strip()

In [27]:
import json
from langchain.text_splitter import RecursiveCharacterTextSplitter

def chunk_text(text: str, chunk_size: int = 512, chunk_overlap: int = 50) -> list[str]:
    """Hàm tiện ích để chia văn bản dài thành các chunk nhỏ hơn."""
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=chunk_size,
        chunk_overlap=chunk_overlap,
        length_function=len
    )
    return text_splitter.split_text(text)

In [28]:
async def process_claims_parallel(retrieved_data):
    evidence_by_claim = {}
    claims = list(retrieved_data.keys())

    async with aiohttp.ClientSession() as session:
        for claim in claims:
            print(f"\n{'='*50}\nHandle claim: '{claim}'")
            documents = retrieved_data[claim]
            all_chunks_for_this_claim = []

            # Gom tất cả link cần crawl
            urls = [doc['link'] for doc in documents]

            # Chạy crawl song song
            print(f"  -> Crawling {len(urls)} links in parallel...")
            tasks = [fetch_content_from_url(u, session) for u in urls]
            full_contents = await asyncio.gather(*tasks)

            # Ghép kết quả với từng doc
            for doc, full_content in zip(documents, full_contents):
                content_to_process = ""

                if full_content and len(full_content) > 100:
                    print(f"SUCCESS!! {doc['link']}")
                    cleaned_full_content = clean_text(full_content)
                    content_to_process = f"{doc.get('title', '')}. {cleaned_full_content}"
                else:
                    print(f"FAIL!! Using snippet for {doc['link']}")
                    cleaned_snippet = clean_text(doc.get('snippet', ''))
                    content_to_process = f"{doc.get('title', '')}. {cleaned_snippet}"

                # Chia nhỏ nội dung
                chunks = chunk_text(content_to_process)

                # Lưu lại
                for chunk_text_part in chunks:
                    all_chunks_for_this_claim.append({
                        "text": chunk_text_part,
                        "link": doc['link']
                    })

            evidence_by_claim[claim] = all_chunks_for_this_claim
            print(f"==> Finish for claim '{claim}'. Total: {len(all_chunks_for_this_claim)} chunks.")

    return evidence_by_claim

In [31]:
# Tải dữ liệu
with open('document_retrieval_results_duckduckgo_v2.json', 'r', encoding='utf-8') as f:
    retrieved_data = json.load(f)
    retrieved_dict = {
    item["claim"]: item["sources"]
    for item in retrieved_data
}

evidence_by_claim = await process_claims_parallel(retrieved_dict)


Handle claim: 'Biến đổi khí hậu đang làm thời tiết cực đoan hơn.'
  -> Crawling 5 links in parallel...
  -> Detect web link. Handle by Trafilatura: https://thanhnien.vn/the-gioi-chiu-ton-that-khung-do-bien-doi-khi-hau-185241111225813102.htm
  -> Detect web link. Handle by Trafilatura: https://nhandan.vn/thich-ung-bien-doi-khi-hau-thuan-thien-ben-vung-post909799.html
  -> Detect web link. Handle by Trafilatura: https://vnexpress.net/luong-co2-toan-cau-dat-muc-cao-ky-luc-4952520.html
  -> Detect web link. Handle by Trafilatura: https://vietnam.un.org/vi/175280-nguyên-nhân-và-ảnh-hưởng-của-biến-đổi-khí-hậu
  -> Detect web link. Handle by Trafilatura: https://suckhoedoisong.vn/thoi-tiet-nhieu-cuc-doan-khong-khi-lanh-bat-dau-xuat-hien-cuoi-thang-9-169250911142833889.htm
✅ SUCCESS! Extracted text using Trafilatura ---
✅ SUCCESS! Extracted text using Trafilatura ---
✅ SUCCESS! Extracted text using Trafilatura ---
✅ SUCCESS! Extracted text using Trafilatura ---
✅ SUCCESS! Extracted text using

In [32]:
HF_TOKEN = os.getenv("HF_TOKEN")

In [ ]:
from sentence_transformers import SentenceTransformer, util

print("Downloading Bi-Encoder model...")
bi_encoder = SentenceTransformer('bkai-foundation-models/vietnamese-bi-encoder')

# Dùng để lưu trữ top-k ứng viên cho mỗi claim
retrieved_candidates_by_claim = {}

# 2. Lặp qua từng claim và các chunk tương ứng của nó
for claim, chunks_for_claim in evidence_by_claim.items():
    print(f"\n--- Finding top-k chunk related to claim: '{claim}' ---")

    if not chunks_for_claim:
        print("     No evidence chunk for this claim")
        retrieved_candidates_by_claim[claim] = []
        continue

    # Encode câu claim hiện tại
    claim_embedding = bi_encoder.encode(claim, convert_to_tensor=True)

    # Lấy danh sách văn bản từ các chunk của claim này
    chunk_texts = [chunk['text'] for chunk in chunks_for_claim]

    # Encode tất cả các chunk
    chunk_embeddings = bi_encoder.encode(chunk_texts, convert_to_tensor=True)

    # 3. Tính cosine similarity cho claim này với các chunk của nó
    cosine_scores = util.cos_sim(claim_embedding, chunk_embeddings)[0]

    # 4. Lấy ra top-k ứng viên tiềm năng
    top_k = 20
    # Đảm bảo top_k không lớn hơn số lượng chunk có sẵn
    num_chunks_available = len(chunks_for_claim)
    actual_top_k = min(top_k, num_chunks_available)

    top_results_indices = cosine_scores.argsort(descending=True)[:actual_top_k]

    # Lưu các ứng viên tốt nhất vào danh sách tạm
    top_chunks_for_this_claim = []
    print(f"    Top {actual_top_k} chunk best related for claim '{claim}':")
    for idx in top_results_indices:
        candidate = chunks_for_claim[idx]
        top_chunks_for_this_claim.append(candidate)
        print(f"    - Score: {cosine_scores[idx]:.4f} - {candidate['text'][:150]}...")

    # Lưu kết quả top-k cho claim hiện tại
    retrieved_candidates_by_claim[claim] = top_chunks_for_this_claim

config.json:   0%|          | 0.00/270 [00:00<?, ?B/s]


--- Finding top-k chunk related to claim: 'Biến đổi khí hậu đang làm thời tiết cực đoan hơn.' ---
    Top 10 chunk best related for claim 'Biến đổi khí hậu đang làm thời tiết cực đoan hơn.':
    - Score: 0.5347 - đảo. Ngoài ra, đại dương hấp thụ cacbon dioxit, giữ cho chúng không bay vào khí quyển. Tuy nhiên quá nhiều cacbon dioxit lại làm tăng tính axit của đạ...
    - Score: 0.4574 - gấp 1.000 lần so với mọi thời điểm từng được ghi nhận trong lịch sử loài người. Một triệu loài sinh vật đang đứng trước nguy cơ tuyệt chủng trong vòng...
    - Score: 0.4437 - Thời tiết nhiều cực đoan , không khí lạnh bắt đầu xuất hiện cuối …. Liên tiếp bão, áp thấp nhiệt đới và mưa lớn bất thường Trong vòng một tháng vừa qu...
    - Score: 0.4167 - tượng cực đoan như dông, lốc, sét, mưa đá, gió giật mạnh vẫn có thể xảy ra ở nhiều nơi, tác động tiêu cực đến sản xuất nông nghiệp, giao thông và đời ...
    - Score: 0.4027 - các hiện tượng thời tiết cực đoan là một trong những lý do làm gia tăng nạn đói cũ

In [35]:
!pip install py_vncorenlp

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 13.5 MB/s eta 0:00:00
  Created wheel for py_vncorenlp: filename=py_vncorenlp-0.1.4-py3-none-any.whl size=4367 sha256=a7cd5582ff32332eb31beb3659122b9ef20e912b50a609fc38c5cba4be5b8800
  Stored in directory: /root/.cache/pip/wheels/db/e5/ff/f4a1b4ece36e8582db1ca71150a34e987e65df50c35974e9bb
Successfully built py_vncorenlp


In [36]:
from sentence_transformers.cross_encoder import CrossEncoder
import py_vncorenlp
import os

In [38]:
!mkdir /content/vncorenlp_model

In [39]:
print("\nLoading VnCoreNLP word segmenter...")
VNCORENLP_SAVE_DIR = '/content/vncorenlp_model'
if not os.path.exists(os.path.join(VNCORENLP_SAVE_DIR, 'model')):
  py_vncorenlp.download_model(save_dir=VNCORENLP_SAVE_DIR)

if 'rdrsegmenter' not in globals():
    rdrsegmenter = py_vncorenlp.VnCoreNLP(annotators=["wseg"], save_dir=VNCORENLP_SAVE_DIR)
else:
    print("VnCoreNLP segmenter already initialized — reusing existing instance.")

# Tải mô hình Cross-Encoder PhoRanker (Vietnamese)
print("\nDownloading PhoRanker Cross-Encoder model...")
MODEL_ID = 'itdainb/PhoRanker'
MAX_LENGTH = 256
cross_encoder = CrossEncoder(MODEL_ID, max_length=MAX_LENGTH)

# Nếu GPU hỗ trợ FP16
try:
    cross_encoder.model.half()
except Exception as e:
    print(f"Warning: Unable to convert model to FP16 ({e})")

# Reranking bằng mô hình PhoRanker
final_evidence_by_claim = {}

for claim, candidates in retrieved_candidates_by_claim.items():
    print(f"\n--- Reranking evidences for claim: '{claim}' ---")

    if not candidates:
        print("     No candidate to rerank.")
        final_evidence_by_claim[claim] = []
        continue

    # Lấy danh sách văn bản ứng viên
    candidate_texts = [candidate['text'] for candidate in candidates]

    # Tách từ và NỐI LẠI THÀNH CHUỖI
    tokenized_claim = " ".join(rdrsegmenter.word_segment(claim))
    tokenized_candidates = [" ".join(rdrsegmenter.word_segment(text)) for text in candidate_texts]

    # Tạo cặp (claim, candidate) ở dạng chuỗi
    tokenized_pairs = [[tokenized_claim, sent] for sent in tokenized_candidates]

    # Dự đoán điểm liên quan
    cross_scores = cross_encoder.predict(tokenized_pairs)

    # Gộp điểm + dữ liệu ứng viên
    reranked_results = list(zip(cross_scores, candidates))
    reranked_results.sort(key=lambda x: x[0], reverse=True)

    # Giới hạn top-k
    final_top_k = 10
    actual_final_top_k = min(final_top_k, len(candidates))
    final_evidence = reranked_results[:actual_final_top_k]

    # Lưu kết quả
    final_evidence_by_claim[claim] = final_evidence

    print(f"    Top {actual_final_top_k} evidences after reranking:")
    for score, chunk in final_evidence:
        print(f"    - Score: {score:.4f} - {chunk['text']} (Source: {chunk.get('link', 'N/A')})")



Loading VnCoreNLP word segmenter...



config.json:   0%|          | 0.00/814 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/540M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

vocab.txt: 0.00B [00:00, ?B/s]

bpe.codes: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

README.md: 0.00B [00:00, ?B/s]


--- Reranking evidences for claim: 'Biến đổi khí hậu đang làm thời tiết cực đoan hơn.' ---
    Top 10 evidences after reranking:
    - Score: 0.7793 - trạng mất năng suất do các hiện tượng thời tiết khắc nghiệt đang được nền kinh tế thực sự cảm nhận ngay tại đây và ngay lúc này". Kim chi Hàn Quốc bị đe dọa bởi biến đổi khí hậu tại quê nhà Ông Denton kêu gọi các nhà lãnh đạo thế giới phản ứng nhanh chóng và đồng bộ trước các tác động kinh tế do thời tiết khắc nghiệt gây ra, đồng thời khẳng định việc "rút hầu bao" cho khí hậu là đầu tư vào một nền kinh tế toàn cầu mạnh mẽ và kiên cường, nơi tất cả mọi người đều được hưởng lợi. Bộ trưởng Môi trường (Source: https://thanhnien.vn/the-gioi-chiu-ton-that-khung-do-bien-doi-khi-hau-185241111225813102.htm)
    - Score: 0.7515 - độ cao và khiến việc thực hiện các công việc ngoài trời trở nên khó khăn hơn. Rủi ro cháy rừng cao hơn và lây lan nhanh hơn rất nhiều khi khí hậu nóng lên. Nhiệt độ ở hai Cực đã tăng lên ít nhất là gấp hai lần so với mức

In [40]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import torch
import json

In [41]:
print("Downloading module NLI (FEVER-trained)...")
nli_model_name = "vicgalle/xlm-roberta-large-xnli-anli"

tokenizer = AutoTokenizer.from_pretrained(nli_model_name)
nli_model = AutoModelForSequenceClassification.from_pretrained(nli_model_name)

def classify_stance(claim: str, evidence_text: str) -> dict:
    """
    Phân loại lập trường của một bằng chứng so với một claim sử dụng mô hình NLI.
    (Hàm này giữ nguyên y hệt như trong notebook gốc của bạn)
    """
    # Mã hóa cặp (bằng chứng, claim)
    # Premise = evidence_text, Hypothesis = claim

    # Cắt bớt văn bản để tránh lỗi token quá dài
    tokenized_input = tokenizer(evidence_text, claim, return_tensors='pt', truncation=True, max_length=512)

    with torch.no_grad():
        outputs = nli_model(**tokenized_input)

    # Lấy điểm số xác suất cho mỗi nhãn
    logits = outputs.logits
    probabilities = torch.softmax(logits, dim=1).squeeze().tolist()

    # Các mô hình XNLI thường có thứ tự nhãn: [contradiction, neutral, entailment]
    # tương ứng với index [0, 1, 2]
    # (Mô hình Moritz này cũng theo thứ tự đó)
    labels = ['Refute', 'Neutral', 'Support']

    # Tìm nhãn có xác suất cao nhất
    predicted_index = torch.argmax(logits, dim=1).item()
    predicted_label = labels[predicted_index]

    return {
        "stance": predicted_label,
        "score": probabilities[predicted_index],
        "scores_all": {
            "refute": probabilities[0],
            "neutral": probabilities[1],
            "support": probabilities[2]
        }
    }

tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/734 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/150 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/2.24G [00:00<?, ?B/s]

In [42]:
results_with_stance = {}

for claim, top_evidence in final_evidence_by_claim.items():
    evidence_with_stance = []
    print(f"\n--- Phân loại lập trường cho claim: '{claim}' ---")

    for score, chunk in top_evidence:
        stance_result = classify_stance(claim, chunk['text'])

        evidence_with_stance.append({
            'text': chunk['text'],
            'link': chunk['link'],
            'rerank_score': score,
            'stance': stance_result['stance'],
            'stance_score': stance_result['score'],
            'stance_scores': stance_result['scores_all']
        })
        print(f"  -> Stance: {stance_result['stance']} ({stance_result['scores_all']}): | Text: {chunk['text']}")

    results_with_stance[claim] = evidence_with_stance


--- Phân loại lập trường cho claim: 'Biến đổi khí hậu đang làm thời tiết cực đoan hơn.' ---
  -> Stance: Neutral ({'refute': 0.001268339459784329, 'neutral': 0.906964123249054, 'support': 0.09176759421825409}): | Text: trạng mất năng suất do các hiện tượng thời tiết khắc nghiệt đang được nền kinh tế thực sự cảm nhận ngay tại đây và ngay lúc này". Kim chi Hàn Quốc bị đe dọa bởi biến đổi khí hậu tại quê nhà Ông Denton kêu gọi các nhà lãnh đạo thế giới phản ứng nhanh chóng và đồng bộ trước các tác động kinh tế do thời tiết khắc nghiệt gây ra, đồng thời khẳng định việc "rút hầu bao" cho khí hậu là đầu tư vào một nền kinh tế toàn cầu mạnh mẽ và kiên cường, nơi tất cả mọi người đều được hưởng lợi. Bộ trưởng Môi trường
  -> Stance: Support ({'refute': 0.0006083848420530558, 'neutral': 0.00215887906961143, 'support': 0.9972327351570129}): | Text: độ cao và khiến việc thực hiện các công việc ngoài trời trở nên khó khăn hơn. Rủi ro cháy rừng cao hơn và lây lan nhanh hơn rất nhiều khi khí hậu nó

## **V. Output**

In [43]:
from collections import Counter
import numpy as np
import os
from azure.ai.inference import ChatCompletionsClient
from azure.ai.inference.models import SystemMessage, UserMessage
from azure.core.credentials import AzureKeyCredential

### 1. HÀM TỔNG HỢP KẾT LUẬN (VERDICT)

In [44]:
def aggregate_verdict_weighted(evidence_with_stance):
    """
    Tổng hợp verdict (True / False / Unknown) dựa trên stance_scores có trọng số.
    """
    if not evidence_with_stance:
        return {"verdict": "Unknown", "confidence": 0.0}

    weights = {"Support": 0.0, "Refute": 0.0, "Neutral": 0.0}
    total_weight = 0.0

    for e in evidence_with_stance:
        s = e["stance_scores"]
        rel = e.get("rerank_score", 1.0)  # nếu có rerank_score thì dùng làm trọng số phụ
        weights["Support"] += s["support"] * rel
        weights["Refute"] += s["refute"] * rel
        weights["Neutral"] += s["neutral"] * rel
        total_weight += rel

    # Chuẩn hóa lại tỷ lệ
    ratio = {k: v / total_weight for k, v in weights.items()}

    if ratio["Support"] > 0.5:
        verdict = "True"
    elif ratio["Refute"] > 0.5:
        verdict = "False"
    else:
        verdict = "Unknown"

    confidence = max(ratio.values())
    return {"verdict": verdict, "confidence": confidence, "stance_ratio": ratio}

### 2. HÀM SINH GIẢI THÍCH (JUSTIFICATION)

In [45]:
# Cấu hình Azure LLM (GPT-4o-mini)
endpoint = "https://models.github.ai/inference"
model = "openai/gpt-4o-mini"
token = os.environ["GITHUB_TOKEN"]

client = ChatCompletionsClient(
    endpoint=endpoint,
    credential=AzureKeyCredential(token)
)

def explain_factcheck_with_best_evidence(claim, verdict, best_evidence, stance_ratio):
    prompt = f"""
Bạn là trợ lý fact-check trung lập và chính xác.
Dưới đây là thông tin hệ thống đã thu thập:

Claim: "{claim}"
System verdict (tổng hợp): {verdict}
Stance ratio (tổng hợp): {stance_ratio}

Best evidence (đã chọn):
"{best_evidence['text']}"
Nguồn: {best_evidence.get('link','(no link)')}

YÊU CẦU (bắt buộc):
- Dựa vào 'System verdict' và 'Stance ratio' khi viết. KHÔNG được mâu thuẫn với verdict đã cho.
- Nếu best evidence ủng hộ nhưng verdict là Unknown, hãy viết theo cấu trúc:
  "[Nhận định]: (True/False/Unknown)"
  "[Giải thích]: Giải thích ngắn (2 câu). Nếu có mâu thuẫn giữa best evidence và verdict, nêu rõ: 'Mặc dù một bằng chứng mạnh cho thấy..., tổng thể bằng chứng hiện nay vẫn...'"

Viết tiếng Việt, 2-3 câu, trung lập và rõ ràng.
"""
    response = client.complete(
        messages=[
            SystemMessage("Bạn là trợ lý fact-check chuyên nghiệp, không mâu thuẫn với verdict đã cho."),
            UserMessage(prompt)
        ],
        model=model,
        temperature=0.2
    )
    return response.choices[0].message.content.strip()

### 3. SINH KẾT LUẬN & IN KẾT QUẢ

In [46]:
final_results = {}

for claim, evidences in results_with_stance.items():
    if not evidences:
        continue

    # Tính verdict có trọng số
    agg = aggregate_verdict_weighted(evidences)

    # Chọn bằng chứng mạnh nhất (score cao nhất)
    best_evidence = max(evidences, key=lambda e: e["stance_score"])

    # Gọi LLM sinh phần giải thích (theo hướng A: tuân thủ verdict)
    justification = explain_factcheck_with_best_evidence(
        claim,
        agg["verdict"],
        best_evidence,
        agg["stance_ratio"]
    )

    # Lưu kết quả
    final_results[claim] = {
        "claim": claim,
        "verdict": agg["verdict"],
        "confidence": agg["confidence"],
        "stance_ratio": agg["stance_ratio"],
        "best_evidence": best_evidence,
        "justification": justification
    }

    # In ra cho người dùng xem
    print("\n" + "="*80)
    print(f"Claim: {claim}")
    print(f"→ Verdict: {agg['verdict']} (Confidence: {agg['confidence']:.2f})")
    print(f"→ Stance ratio: {agg['stance_ratio']}")
    print(f"→ Best Evidence (score={best_evidence['stance_score']:.2f}):")
    print(f"{best_evidence['text'][:300]}...")
    print(f"[Source: {best_evidence['link']}]")
    print("→ Giải thích kiểm chứng:")
    print(justification)


Claim: Biến đổi khí hậu đang làm thời tiết cực đoan hơn.
→ Verdict: True (Confidence: 0.67)
→ Stance ratio: {'Support': np.float32(0.66965103), 'Refute': np.float32(0.0024213602), 'Neutral': np.float32(0.3279276)}
→ Best Evidence (score=1.00):
Biến đổi khí hậu nghiêm trọng do nồng độ khí nhà kính tăng cao. Theo Live Science, lượng carbon dioxide (CO2) thải vào khí quyển của Trái Đất tăng ở mức kỷ lục trong năm 2024. Nồng độ CO2 tăng thêm 3,5 phần triệu (ppm) từ năm 2023 đến 2024, đánh dấu mức tăng lớn nhất trong một năm kể từ năm 1957. Cá...
[Source: https://vnexpress.net/luong-co2-toan-cau-dat-muc-cao-ky-luc-4952520.html]
→ Giải thích kiểm chứng:
[Nhận định]: True  
[Giải thích]: Biến đổi khí hậu do nồng độ khí nhà kính tăng cao đang dẫn đến thời tiết cực đoan hơn, như được chỉ ra bởi sự gia tăng kỷ lục của lượng CO2 trong khí quyển. Mặc dù có nhiều yếu tố ảnh hưởng đến thời tiết, nhưng bằng chứng hiện tại cho thấy biến đổi khí hậu có vai trò quan trọng trong việc làm gia tăng tính c